*Import librairies*

In [32]:
import yfinance as yf
import pandas as pd
import csv
from tqdm.notebook import tqdm
import html5lib
import plotly_dark_custom
import plotly.express as px
from datetime import datetime
import plotly.io as pio
import plotly_dark_custom
import plotly.graph_objects as go
import plotly.figure_factory as ff
from plotly.subplots import make_subplots
import numpy as np
import plotly.offline as pyo
from scipy.stats import linregress, norm

pyo.init_notebook_mode()
pd.set_option("display.max_columns", 101)

*VARIABLES*

In [33]:
WIDTH = 900 
HEIGHT = 600

app_color = {
    "graph_bg": "rgb(221, 236, 255)",
    "graph_line": "rgb(8, 70, 151)",
    "graph_font":"rgb(2, 29, 65)"
}

chart_colors = [
    '#664DFF',
    '#893BFF',
    '#3CC5E8',
    '#2C93E8',
    '#0BEBDD',
    '#0073FF',
    '#00BDFF',
    '#A5E82C',
    '#FFBD42',
    '#FFCA30'
]

pio.templates.default = "plotly_dark_custom"

*Functions*

In [34]:
# Compute Statistics
def get_statistics(data, returns, market, stocks_name=None, only_one=True, name='S&P500'):
    if only_one:
        stats = pd.DataFrame(
            {
                'Std': [data[returns].std()],
                'Annual Std': [data[returns].std()* np.sqrt(252)],
                'Mean': [data[returns].mean()],
                'Median': [np.median(data[returns].std())],
                'Min': [data[returns].min()],
                'Max': [data[returns].max()],
                'Kurtosis': [data[returns].kurtosis()],
                'Skewness': [data[returns].skew()],
                'Alpha': [linregress(data[returns], market[returns]).intercept],
                'Beta': [linregress(data[returns], market[returns]).slope],
                'VaR 95% HS': [data[returns].sort_values(ascending=True).quantile(0.05)],
                'VaR 95% DN': [norm.ppf(1-0.95, data[returns].mean(), data[returns].std())],
                'Systemic Risk': [linregress(data[returns], market[returns]).slope**2 * market[returns].var()]
            },
            index=[name]
        ).round(6)
    else:
        stats = pd.DataFrame(
            {
                'Std': [data[name, returns].std() for name in stocks_name],
                'Annual Std': [data[name, returns].std()* np.sqrt(252) for name in stocks_name],
                'Mean': [data[name, returns].mean() for name in stocks_name],
                'Median': [np.median(data[name, returns]) for name in stocks_name],
                'Min': [data[name, returns].min() for name in stocks_name],
                'Max': [data[name, returns].max() for name in stocks_name],
                'Kurtosis': [data[name, returns].kurtosis() for name in stocks_name],
                'Skewness': [data[name, returns].skew() for name in stocks_name],
                'Alpha': [linregress(data[name, returns], market[returns]).intercept for name in stocks_name],
                'Beta': [linregress(data[name, returns], market[returns]).slope for name in stocks_name],
                'VaR 95% HS': [data[name, returns].sort_values(ascending=True).quantile(0.05) for name in stocks_name],
                'VaR 95% DN': [norm.ppf(1-0.95, data[name, returns].mean(), data[name, returns].std()) for name in stocks_name],
                'Systemic Risk': [linregress(data[name, returns], market[returns]).slope**2 * market[returns].var() for name in stocks_name],
            },
            index=[name for name in stocks_name]
        ).round(6)

    return stats

# ESSAY 1

## Introduction

### Stocks

In [35]:
stocks = {
 'Materials': {'Name': 'Newmont Corporation', 'Ticker': 'NEM'},
 'Communication Services': {'Name': 'Alphabet Inc.', 'Ticker': 'GOOGL'},
 'Consumer Discretionary': {'Name': 'Amazon.com Inc.', 'Ticker': 'AMZN'},
 'Consumer Staples': {'Name': 'PepsiCo Inc.', 'Ticker': 'PEP'},
 'Energy': {'Name': 'National Oilwell Varco Inc.', 'Ticker': 'NOV'},
 'Financial Services': {'Name': 'Bank of America Corp', 'Ticker': 'BAC'},
 'Healthcare': {'Name': 'HCA Healthcare', 'Ticker': 'HCA'},
 'Industrials': {'Name': 'Boeing Company', 'Ticker': 'BA'},
 'Real Estate': {'Name': 'Host Hotels & Resorts', 'Ticker': 'HST'},
 'Information Technology': {'Name': 'Apple Inc.', 'Ticker': 'AAPL'},
 'Utilities': {'Name': 'American Electric Power', 'Ticker': 'AEP'}
}

### Downloading data

In [36]:
data = yf.download(
        tickers = [stocks[stock]['Ticker'] for stock in stocks],
        group_by = 'ticker',
        start="2018-06-30"
    )

[*********************100%***********************]  11 of 11 completed


In [37]:
market = yf.download(
    tickers = "^GSPC",
    start="2018-06-30"
)

market.dropna(inplace=True)
market['Returns'] = market.Open.pct_change()
market['Logs'] = np.log(market.Open) - np.log(market.Open.shift(1))
market.dropna(inplace=True)

[*********************100%***********************]  1 of 1 completed


In [38]:
stocks_name = []
for ticks in data.columns.levels[0]:
    for stock in stocks:
        if ticks == stocks[stock]['Ticker']:
            stocks_name.append(stocks[stock]['Name'])

In [39]:
data.columns.set_levels(stocks_name, level=0, inplace=True)

In [40]:
data['Apple Inc.']

Open        High         Low       Close   Adj Close  \
Date                                                                     
2018-06-29   46.572498   46.797501   45.727501   46.277500   44.964947   
2018-07-02   45.955002   46.825001   45.855000   46.794998   45.467773   
2018-07-03   46.947498   46.987499   45.884998   45.980000   44.675892   
2018-07-05   46.314999   46.602501   46.070000   46.349998   45.035393   
2018-07-06   46.355000   47.107498   46.299999   46.992500   45.659668   
...                ...         ...         ...         ...         ...   
2020-10-15  118.720001  121.199997  118.150002  120.709999  120.709999   
2020-10-16  121.279999  121.550003  118.809998  119.019997  119.019997   
2020-10-19  119.959999  120.419998  115.660004  115.980003  115.980003   
2020-10-20  116.199997  118.980003  115.629997  117.510002  117.510002   
2020-10-21  116.669998  118.705002  116.449997  118.224998  118.224998   

                 Volume  
Date                     
2018-06-29   90950800.0  
2018-07-02   70925200.0  
2018-07-03   55819200.0  
2018-07-05   66416800.0  
2018-07-06   69940800.0  
...                 ...  
2020-10-15  112559200.0  
2020-10-16  115393800.0  
2020-10-19  120639300.0  
2020-10-20  124004200.0  
2020-10-21   25101762.0  

[584 rows x 6 columns]

### Statistics about stocks

In [41]:
data.dropna(inplace=True)

In [42]:
for name in stocks_name: 
    data[name, 'Returns'] = data[name].Open.pct_change()

In [43]:
for name in stocks_name: 
    data[name, 'Logs'] = np.log(data[name].Open) - np.log(data[name].Open.shift(1))

In [44]:
data.sort_index(axis=1, inplace=True)
data.dropna(inplace=True)

In [45]:
data.describe(include='all')

Alphabet Inc.                                                     \
          Adj Close        Close         High        Logs          Low   
count    582.000000   582.000000   582.000000  582.000000   582.000000   
mean    1260.974991  1260.974991  1273.783624    0.000561  1246.813120   
std      154.722362   154.722362   155.621489    0.019272   153.492822   
min      984.669983   984.669983  1012.119995   -0.106093   977.659973   
25%     1141.005035  1141.005035  1150.207550   -0.008355  1124.032471   
50%     1218.264954  1218.264954  1231.375000    0.001707  1209.119995   
75%     1384.970032  1384.970032  1398.239960    0.010946  1354.799988   
max     1717.390015  1717.390015  1726.099976    0.075280  1660.189941   

                                             Amazon.com Inc.               \
              Open     Returns        Volume       Adj Close        Close   
count   582.000000  582.000000  5.820000e+02      582.000000   582.000000   
mean   1260.208488    0.000746  1.816805e+06     2056.529656  2056.529656   
std     154.259024    0.019170  8.517933e+05      501.987905   501.987905   
min     984.320007   -0.100659  6.401000e+05     1343.959961  1343.959961   
25%    1137.037506   -0.008320  1.276275e+06     1761.834961  1761.834961   
50%    1220.299988    0.001709  1.583350e+06     1863.654968  1863.654968   
75%    1380.562469    0.011006  2.079350e+06     2050.089966  2050.089966   
max    1699.520020    0.078186  6.658900e+06     3531.449951  3531.449951   

                                                                      \
              High        Logs          Low         Open     Returns   
count   582.000000  582.000000   582.000000   582.000000  582.000000   
mean   2080.717225    0.001076  2030.476667  2056.854107    0.001346   
std     511.872401    0.023239   492.612003   503.283323    0.023214   
min    1396.030029   -0.110622  1307.000000  1346.000000   -0.104723   
25%    1777.105011   -0.009866  1742.655029  1760.097534   -0.009817   
50%    1881.570007    0.001817  1845.820007  1860.500000    0.001819   
75%    2068.215027    0.012518  2030.200012  2043.722534    0.012597   
max    3552.250000    0.099056  3486.689941  3547.000000    0.104128   

                    American Electric Power                          \
             Volume               Adj Close       Close        High   
count  5.820000e+02              582.000000  582.000000  582.000000   
mean   4.773266e+06               81.168895   83.895172   84.652784   
std    2.195037e+06                9.037256    8.359211    8.384419   
min    8.813000e+05               63.994541   68.870003   69.239998   
25%    3.148850e+06               74.553196   77.750000   78.579998   
50%    4.233350e+06               81.496002   83.615002   84.650002   
75%    5.783350e+06               87.928864   90.467503   91.187502   
max    1.556730e+07              102.555588  104.330002  104.970001   

                                                                     \
             Logs         Low        Open     Returns        Volume   
count  582.000000  582.000000  582.000000  582.000000  5.820000e+02   
mean     0.000462   82.995584   83.845292    0.000617  2.723149e+06   
std      0.017714    8.408497    8.359059    0.017509  1.377793e+06   
min     -0.130870   65.139999   68.639999   -0.122668  3.836470e+05   
25%     -0.005890   76.695002   77.492498   -0.005873  2.015350e+06   
50%      0.001012   82.810001   83.660000    0.001013  2.402650e+06   
75%      0.008431   89.657503   90.502502    0.008466  3.104450e+06   
max      0.082385  103.860001  104.470001    0.085874  2.245570e+07   

       Apple Inc.                                                              \
        Adj Close       Close        High        Logs         Low        Open   
count  582.000000  582.000000  582.000000  582.000000  582.000000  582.000000   
mean    64.048265   64.681100   65.421284    0.001578   63.846499   64.612771   
std     22.578863   22.2734

#### Normal returns

In [46]:
stocks_stats = get_statistics(data=data, returns='Returns', market=market, stocks_name=stocks_name, only_one=False)

In [47]:
market_stats = get_statistics(data=market, returns='Returns', market=market)

In [48]:
market_stats

Std  Annual Std      Mean    Median      Min     Max  Kurtosis  \
S&P500  0.012074    0.191671  0.000472  0.012074 -0.06892  0.0622  5.475152   

        Skewness  Alpha  Beta  VaR 95% HS  VaR 95% DN  Systemic Risk  
S&P500 -0.620756    0.0   1.0   -0.021036   -0.019388       0.000146

In [49]:
stocks_stats

Std  Annual Std      Mean    Median  \
Alphabet Inc.                0.019170    0.304308  0.000746  0.001709   
Amazon.com Inc.              0.023214    0.368508  0.001346  0.001819   
Boeing Company               0.039061    0.620079 -0.000442 -0.001108   
HCA Healthcare               0.028828    0.457634  0.000884  0.001220   
Host Hotels & Resorts        0.027248    0.432545 -0.000708  0.000000   
National Oilwell Varco Inc.  0.038979    0.618778 -0.001897 -0.002626   
Newmont Corporation          0.026628    0.422710  0.001238  0.001496   
Apple Inc.                   0.022746    0.361080  0.001838  0.003353   
Bank of America Corp         0.024913    0.395484 -0.000003  0.000838   
PepsiCo Inc.                 0.013398    0.212689  0.000521  0.000579   
American Electric Power      0.017509    0.277948  0.000617  0.001013   

                                  Min       Max   Kurtosis  Skewness  \
Alphabet Inc.               -0.100659  0.078186   3.501700 -0.529419   
Amazon.com Inc.             -0.104723  0.104128   2.954049 -0.087567   
Boeing Company              -0.280102  0.252456  15.582689  0.112782   
HCA Healthcare              -0.154176  0.271642  17.823047  0.999585   
Host Hotels & Resorts       -0.154278  0.151581   7.921804  0.378365   
National Oilwell Varco Inc. -0.328736  0.242459  12.326322 -0.535697   
Newmont Corporation         -0.251144  0.180919  19.514744 -0.997782   
Apple Inc.                  -0.086602  0.097256   2.898988 -0.216439   
Bank of America Corp        -0.127208  0.126021   6.573329 -0.150273   
PepsiCo Inc.                -0.103518  0.051992   9.401855 -1.188849   
American Electric Power     -0.122668  0.085874  11.447133 -1.180419   

                                Alpha      Beta  VaR 95% HS  VaR 95% DN  \
Alphabet Inc.                0.000132  0.455621   -0.029562   -0.030785   
Amazon.com Inc.              0.000042  0.319539   -0.034523   -0.036837   
Boeing Company               0.000554  0.185877   -0.053886   -0.064692   
HCA Healthcare               0.000258  0.241838   -0.038656   -0.046534   
Host Hotels & Resorts        0.000648  0.247959   -0.039631   -0.045526   
National Oilwell Varco Inc.  0.000780  0.162177   -0.059732   -0.066012   
Newmont Corporation          0.000366  0.085738   -0.035023   -0.042561   
Apple Inc.                  -0.000219  0.376043   -0.036627   -0.035576   
Bank of America Corp         0.000473  0.326892   -0.037057   -0.040982   
PepsiCo Inc.                 0.000201  0.519585   -0.019493   -0.021517   
American Electric Power      0.000301  0.277776   -0.021293   -0.028183   

                             Systemic Risk  
Alphabet Inc.                     0.000030  
Amazon.com Inc.                   0.000015  
Boeing Company                    0.000005  
HCA Healthcare                    0.000009  
Host Hotels & Resorts             0.000009  
National Oilwell Varco Inc.       0.000004  
Newmont Corporation               0.000001  
Apple Inc.                        0.000021  
Bank of America Corp              0.000016  
PepsiCo Inc.                      0.000039  
American Electric Power           0.000011

#### Log Returns

In [50]:
market_stats_logs = get_statistics(data=market, returns='Logs', market=market)

In [51]:
stocks_stats_logs = get_statistics(data=data, returns='Logs', market=market, stocks_name=stocks_name, only_one=False) 

In [52]:
market_stats_logs

Std  Annual Std      Mean   Median      Min       Max  Kurtosis  \
S&P500  0.01212      0.1924  0.000399  0.01212 -0.07141  0.060343  5.662037   

        Skewness  Alpha  Beta  VaR 95% HS  VaR 95% DN  Systemic Risk  
S&P500 -0.748911    0.0   1.0    -0.02126   -0.019537       0.000147

In [53]:
stocks_stats_logs

Std  Annual Std      Mean    Median  \
Alphabet Inc.                0.019272    0.305938  0.000561  0.001707   
Amazon.com Inc.              0.023239    0.368901  0.001076  0.001817   
Boeing Company               0.039513    0.627243 -0.001213 -0.001108   
HCA Healthcare               0.028586    0.453790  0.000474  0.001219   
Host Hotels & Resorts        0.027225    0.432176 -0.001078  0.000000   
National Oilwell Varco Inc.  0.039944    0.634092 -0.002681 -0.002630   
Newmont Corporation          0.027163    0.431200  0.000875  0.001495   
Apple Inc.                   0.022790    0.361777  0.001578  0.003347   
Bank of America Corp         0.025026    0.397273 -0.000315  0.000838   
PepsiCo Inc.                 0.013511    0.214479  0.000431  0.000579   
American Electric Power      0.017714    0.281198  0.000462  0.001012   

                                  Min       Max   Kurtosis  Skewness  \
Alphabet Inc.               -0.106093  0.075280   3.799966 -0.681273   
Amazon.com Inc.             -0.110622  0.099056   3.077653 -0.260153   
Boeing Company              -0.328646  0.225106  17.989162 -0.963049   
HCA Healthcare              -0.167444  0.240309  13.905620  0.277815   
Host Hotels & Resorts       -0.167564  0.141136   8.081206 -0.024547   
National Oilwell Varco Inc. -0.398592  0.217093  19.222095 -1.519909   
Newmont Corporation         -0.289208  0.166293  26.778593 -1.926192   
Apple Inc.                  -0.090584  0.092812   2.936530 -0.380083   
Bank of America Corp        -0.136059  0.118690   6.805810 -0.469612   
PepsiCo Inc.                -0.109277  0.050685  10.721858 -1.398775   
American Electric Power     -0.130870  0.082385  12.792595 -1.505433   

                                Alpha      Beta  VaR 95% HS  VaR 95% DN  \
Alphabet Inc.                0.000142  0.457434   -0.030008   -0.031139   
Amazon.com Inc.              0.000050  0.323781   -0.035133   -0.037148   
Boeing Company               0.000621  0.183363   -0.055392   -0.066205   
HCA Healthcare               0.000282  0.246277   -0.039423   -0.046546   
Host Hotels & Resorts        0.000668  0.249987   -0.040438   -0.045858   
National Oilwell Varco Inc.  0.000823  0.158089   -0.061591   -0.068383   
Newmont Corporation          0.000321  0.089018   -0.035651   -0.043804   
Apple Inc.                  -0.000197  0.377853   -0.037314   -0.035908   
Bank of America Corp         0.000502  0.328257   -0.037761   -0.041479   
PepsiCo Inc.                 0.000175  0.519677   -0.019686   -0.021793   
American Electric Power      0.000270  0.279174   -0.021523   -0.028675   

                             Systemic Risk  
Alphabet Inc.                     0.000031  
Amazon.com Inc.                   0.000015  
Boeing Company                    0.000005  
HCA Healthcare                    0.000009  
Host Hotels & Resorts             0.000009  
National Oilwell Varco Inc.       0.000004  
Newmont Corporation               0.000001  
Apple Inc.                        0.000021  
Bank of America Corp              0.000016  
PepsiCo Inc.                      0.000040  
American Electric Power           0.000011

**Apple Analysis**

In [54]:
fig = px.line(x=data['Apple Inc.'].index, y=data['Apple Inc.'].Close)
fig.update_xaxes(rangeslider_visible=True)

fig.update_layout(
    width=WIDTH, 
    height=HEIGHT,
    title='Apple Analysis during the COVID',
    yaxis_title='Closing Price',
    xaxis_title='Date',
    shapes = [dict(
        x0='2020-02-15', x1='2020-02-15', y0=0, y1=1, xref='x', yref='paper',
        line_width=2)],
    annotations=[dict(
        x='2020-02-17', y=0.95, xref='x', yref='paper',
        showarrow=False, xanchor='left', text='COVID Begins')],
    yaxis=dict(
    ticksuffix=' $'
    ),

)

pyo.iplot(fig, filename='jupyter-basic_bar')

**Amazon Analysis**

In [55]:
fig = go.Figure(data=[go.Candlestick(x=data['Amazon.com Inc.'].index,
                open=data['Amazon.com Inc.'].Open,
                high=data['Amazon.com Inc.'].High,
                low=data['Amazon.com Inc.'].Low,
                close=data['Amazon.com Inc.'].Close)])

fig.update_layout(
    width=WIDTH, 
    height=HEIGHT,
    title='Amazon.com Analysis during the COVID',
    yaxis_title='Prices',
    shapes = [dict(
        x0='2020-02-15', x1='2020-02-15', y0=0, y1=1, xref='x', yref='paper',
        line_width=2)],
    annotations=[dict(
        x='2020-02-17', y=0.95, xref='x', yref='paper',
        showarrow=False, xanchor='left', text='COVID Begins')],
    yaxis=dict(
    ticksuffix=' $'
    ),
)

pyo.iplot(fig, filename='test')

**Boeing Company Analysis**

In [56]:
colors = np.where(data['Boeing Company'].Returns < 0, 'red', 'green')

# Create figure with secondary y-axis
fig = make_subplots(specs=[[{"secondary_y": True}]])

# Add traces
fig.add_trace(
    go.Scatter(x=data['Boeing Company'].index, y=data['Boeing Company'].Close, name="Closing Prices", yaxis="y"),
    secondary_y=False
)

fig.add_trace(
    go.Bar(x=data['Boeing Company'].index, y=(data['Boeing Company'].Returns * 100), name="Returns", marker_color=colors, yaxis="y1"),
    secondary_y=True
)

# Set x-axis title
fig.update_xaxes(title_text="Date")

# Set y-axes titles
# fig.update_yaxes(title_text="<b>primary</b> yaxis title", secondary_y=False)
# fig.update_yaxes(title_text="<b>secondary</b> yaxis title", secondary_y=True)

fig.update_layout(
    width=WIDTH, 
    height=HEIGHT,
    title='Boeing Company Analysis during the COVID',
    yaxis=dict(
    title="TSLA Close's Prices",
    ticksuffix=' $'

    ),
    yaxis2=dict(
        title="TSLA Returns",
        ticksuffix = '%'
    ),
    shapes = [dict(
        x0='2020-02-15', x1='2020-02-15', y0=0, y1=1, xref='x', yref='paper',
        line_width=2)],
    annotations=[dict(
        x='2020-02-17', y=0.95, xref='x', yref='paper',
        showarrow=False, xanchor='left', text='COVID Begins')]
)

pyo.iplot(fig)

**Compare Stocks**

In [57]:
fig = go.Figure()

visible = [False] * len(stocks_name)
visible[0] = True

for i, name in enumerate(stocks_name):
    fig.add_trace(
        go.Scatter(
            x = data[name].index,
            y = data[name].Close,
            name = name,
            visible=visible[i]
        )
    )

buttons = []

for i, name in enumerate(stocks_name):
    false_true = [False] * len(stocks_name)
    false_true[i] = True
    buttons.append(
        dict(label = name,
                method = 'update',
                args = [{'visible': false_true}])
    )

fig.update_layout(

    updatemenus=[
        dict(buttons=buttons,
        direction="down",
        pad={"r": 10, "t": 10},
        x=0.8,
        xanchor="left",
        y=1.2,
        yanchor="top",
        active=0,
        )],
)


fig.update_layout(
    width=WIDTH, 
    height=HEIGHT,
    title='Two years in S&P500',
    yaxis_title='Closing Prices',
    shapes = [dict(
        x0='2020-02-15', x1='2020-02-15', y0=0, y1=1, xref='x', yref='paper',
        line_width=2)],

    annotations=[
        dict(x='2020-02-17', y=0.95, xref='x', yref='paper',
        showarrow=False, xanchor='left', text='COVID Begins'),
        
        dict(text="Choose Stocks:", showarrow=False,x=0.61,
        xanchor='left', y=1.17, yanchor="top",
        yref='paper', xref='paper',
        font=dict(size=18))
        ],

    yaxis=dict(
    ticksuffix=' $'
    ),
)


pyo.iplot(fig)

## Question 1

## Question 2

### Equal Weighted Portfolio

In [58]:
weights = [100 / len(stocks_name) for i in range(len(stocks_name))]

equal_weighted_portfolio_norm_returns = pd.concat([data[name, 'Returns']*weight for name, weight in zip(stocks_name, weights)], axis=1).sum(axis=1)
equal_weighted_portfolio_logs_returns = pd.concat([data[name, 'Logs']*weight for name, weight in zip(stocks_name, weights)], axis=1).sum(axis=1)

equal_weighted_portfolio_returns = pd.concat([equal_weighted_portfolio_norm_returns, equal_weighted_portfolio_logs_returns], axis=1)
equal_weighted_portfolio_returns.columns = ['Returns', 'Logs']

In [59]:
eq_w_portfolio_stats = get_statistics(data=equal_weighted_portfolio_returns, returns='Returns', market=market, name='Eq W Portfolio')

In [60]:
eq_w_portfolio_stats

Std  Annual Std      Mean    Median        Min       Max  \
Eq W Portfolio  1.700039   26.987281  0.037656  1.700039 -12.298045  9.696101   

                 Kurtosis  Skewness     Alpha      Beta  VaR 95% HS  \
Eq W Portfolio  11.479926 -0.881388  0.000248  0.005949   -2.514732   

                VaR 95% DN  Systemic Risk  
Eq W Portfolio   -2.758659            0.0

## Question 3

### Efficient portfolio

In [134]:
%%time

log_ret = pd.concat([data[name, 'Logs'] for name in stocks_name], axis=1)
log_ret.columns = log_ret.columns.droplevel(1)

np.random.seed(42)
num_ports = 10000
all_weights = np.zeros((num_ports, len(log_ret.columns)))
ret_arr = np.zeros(num_ports)
vol_arr = np.zeros(num_ports)
sharpe_arr = np.zeros(num_ports)


for x in range(num_ports):
    # Weights
    weights = np.array(np.random.random(len(stocks)))
    weights = weights/np.sum(weights)

    # Save weights
    all_weights[x,:] = weights

    # Expected return
    ret_arr[x] = np.sum( (log_ret.mean() * weights * 252))

    # Expected volatility
    vol_arr[x] = np.sqrt(np.dot(weights.T, np.dot(log_ret.cov()*252, weights)))

    # Sharpe Ratio
    sharpe_arr[x] = ret_arr[x]/vol_arr[x]


max_sr_ret, max_sr_vol = ret_arr[sharpe_arr.argmax()], vol_arr[sharpe_arr.argmax()]
min_vol_ret, min_vol_vol = ret_arr[vol_arr.argmin()], vol_arr[vol_arr.argmin()]

weights_max_sharpe = list(all_weights[sharpe_arr.argmax()])
weights_min_vol = list(all_weights[vol_arr.argmin()])

max_sharpe_allocation = pd.DataFrame([i*100 for i in weights_max_sharpe],index=log_ret.columns,columns=['Max Sharpe Allocation'])
min_vol_allocation = pd.DataFrame([i*100 for i in weights_min_vol],index=log_ret.columns,columns=['Min Volatility Allocation'])

allocation = max_sharpe_allocation.T.append(min_vol_allocation.T)

allocation['Returns'] = [max_sr_ret*100, min_vol_ret*100]
allocation['Volatility'] = [max_sr_vol*100, min_vol_vol*100]

allocation = allocation.round(2)
allocation

CPU times: user 8.46 s, sys: 0 ns, total: 8.46 s
Wall time: 8.46 s


Alphabet Inc.  Amazon.com Inc.  Boeing Company  \
Max Sharpe Allocation              12.35            14.32            1.18   
Min Volatility Allocation          15.36            11.69            0.41   

                           HCA Healthcare  Host Hotels & Resorts  \
Max Sharpe Allocation               20.44                   0.46   
Min Volatility Allocation            6.48                   3.66   

                           National Oilwell Varco Inc.  Newmont Corporation  \
Max Sharpe Allocation                             0.18                 4.97   
Min Volatility Allocation                         1.18                17.92   

                           Apple Inc.  Bank of America Corp  PepsiCo Inc.  \
Max Sharpe Allocation           21.81                  1.59         19.20   
Min Volatility Allocation        3.03                  8.25         22.57   

                           American Electric Power  Returns  Volatility  
Max Sharpe Allocation                         3.49    19.60       24.92  
Min Volatility Allocation                     9.45    12.25       22.15

In [135]:
efficient_frontier = go.Figure(go.Scatter(
    x=vol_arr,
    y=ret_arr,
    marker=dict(
        size=5,
        color=sharpe_arr,
        colorbar=dict(
            title="Colorbar"
        ),
    ),
    mode="markers",
    name=f"Portfolios ({num_ports})"))

efficient_frontier.add_trace(go.Scatter(
    x=[max_sr_vol],
    y=[max_sr_ret],
    marker={'color':'red'},
    mode='markers',
    name='Efficient Portfolio'
))

efficient_frontier.add_trace(go.Scatter(
    x=[min_vol_vol],
    y=[min_vol_ret],
    marker={'color':'orange'},
    mode='markers',
    marker_symbol='x',
    name='Min Volatility Portfolio'
))

efficient_frontier.update_layout(
    height=HEIGHT,
    width=WIDTH,
    legend=dict(
        yanchor="top",
        y=1.2,
        xanchor="left",
        x=1
        ),
    title='Simulated Portfolio Optimization based on Efficient Frontier'
)            


pyo.iplot(efficient_frontier)

# Plot the efficient frontier